# Imports

In [18]:
import os
from typing import TYPE_CHECKING, Union, cast

import git
import matplotlib.pyplot as plt
import numpy as np

import habitat
from habitat.config.default_structured_configs import (
    CollisionsMeasurementConfig,
    FogOfWarConfig,
    TopDownMapMeasurementConfig,
)
from habitat.core.agent import Agent
from habitat.tasks.nav.nav import NavigationEpisode, NavigationGoal
from habitat.tasks.nav.shortest_path_follower import ShortestPathFollower
from habitat.utils.visualizations import maps
from habitat.utils.visualizations.utils import (
    images_to_video,
    observations_to_image,
    overlay_frame,
)
from habitat_sim.utils import viz_utils as vut

# Quiet the Habitat simulator logging
os.environ["MAGNUM_LOG"] = "quiet"
os.environ["HABITAT_SIM_LOG"] = "quiet"

if TYPE_CHECKING:
    from habitat.core.simulator import Observations
    from habitat.sims.habitat_simulator.habitat_simulator import HabitatSim

repo = git.Repo(".", search_parent_directories=True)
dir_path = os.path.join(repo.working_tree_dir, "simulation/")
data_path = os.path.join(dir_path, "simulation/data/")
output_path = os.path.join(dir_path, "simulation/output/")
os.makedirs(output_path, exist_ok=True)
os.chdir(dir_path)

print(f"Dir path: {dir_path} \nData path: {data_path} \nOutput path: {output_path}")

Dir path: /home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/ 
Data path: /home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/ 
Output path: /home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/output/


# Download the Matterport3D datasets

In [28]:
!python -m habitat_sim.utils.datasets_download --uids habitat_test_scenes habitat_test_pointnav_dataset --data-path {data_path} --no-replace

Found the existing repo for (habitat_test_scenes): /home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/versioned_data/habitat_test_scenes
 checking out main and pulling changes from repo.
Not replacing data, generating symlink (/home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/scene_datasets/habitat-test-scenes).
Generating symlink (/home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/scene_datasets/habitat-test-scenes).
Existing data source (habitat_test_pointnav_dataset) version (1.0) is current. Data located: '/home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/versioned_data/habitat_test_pointnav_dataset_1.0'. Symblink: '/home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/datasets/pointnav/habitat-test-scenes'.
Not replacing data, generating symlink (/home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/data/datasets/pointnav/habitat-test-scenes).
Generating symli

In [33]:
class ShortestPathFollowerAgent(Agent):
    r"""Implementation of the :ref:`habitat.core.agent.Agent` interface that
    uses :ref`habitat.tasks.nav.shortest_path_follower.ShortestPathFollower` utility class
    for extracting the action on the shortest path to the goal.
    """

    def __init__(self, env: habitat.Env, goal_radius: float):
        self.env = env
        self.shortest_path_follower = ShortestPathFollower(
            sim=cast("HabitatSim", env.sim),
            goal_radius=goal_radius,
            return_one_hot=False,
        )

    def act(self, observations: "Observations") -> Union[int, np.ndarray]:
        return self.shortest_path_follower.get_next_action(
            cast(NavigationEpisode, self.env.current_episode).goals[0].position
        )

    def reset(self) -> None:
        pass


config = habitat.get_config(
    config_path=os.path.join(
        dir_path,
        "habitat-lab/habitat/config/benchmark/nav/pointnav/pointnav_habitat_test.yaml",
    )
)

# Add habitat.tasks.nav.nav.TopDownMap and habitat.tasks.nav.nav.Collisions measures
with habitat.config.read_write(config):
    config.habitat.task.measurements.update(
        {
            "top_down_map": TopDownMapMeasurementConfig(
                map_padding=3,
                map_resolution=1024,
                draw_source=True,
                draw_border=True,
                draw_shortest_path=True,
                draw_view_points=True,
                draw_goal_positions=True,
                draw_goal_aabbs=True,
                fog_of_war=FogOfWarConfig(
                    draw=True,
                    visibility_dist=5.0,
                    fov=90,
                ),
            ),
            "collisions": CollisionsMeasurementConfig(),
        }
    )
    
# Create dataset
dataset = habitat.make_dataset(id_dataset=config.habitat.dataset.type, config=config.habitat.dataset)
# Create simulation environment
with habitat.Env(config=config, dataset=dataset) as env:
    # Create ShortestPathFollowerAgent agent
    agent = ShortestPathFollowerAgent(
        env=env,
        goal_radius=config.habitat.task.measurements.success.success_distance,
    )
    # Create video of agent navigating in the first episode
    num_episodes = 1
    for _ in range(num_episodes):
        # Load the first episode and reset agent
        observations = env.reset()
        agent.reset()

        # Get metrics
        info = env.get_metrics()
        # Concatenate RGB-D observation and topdowm map into one image
        frame = observations_to_image(observations, info)

        # Remove top_down_map from metrics
        info.pop("top_down_map")
        # Overlay numeric metrics onto frame
        frame = overlay_frame(frame, info)
        # Add fame to vis_frames
        vis_frames = [frame]

        # Repeat the steps above while agent doesn't reach the goal
        while not env.episode_over:
            # Get the next best action
            action = agent.act(observations)
            if action is None:
                break

            # Step in the environment
            observations = env.step(action)
            info = env.get_metrics()
            frame = observations_to_image(observations, info)

            info.pop("top_down_map")
            frame = overlay_frame(frame, info)
            vis_frames.append(frame)

        current_episode = env.current_episode
        video_name = f"{os.path.basename(current_episode.scene_id)}_{current_episode.episode_id}"
        # Create video from images and save to disk
        images_to_video(
            vis_frames, output_path, video_name, fps=6, quality=9
        )
        vis_frames.clear()
        # Display video
        vut.display_video(f"{output_path}/{video_name}.mp4")


2024-05-02 14:48:36,457 Initializing dataset PointNav-v1
2024-05-02 14:48:36,584 initializing sim Sim-v0
[14:48:36:601703]:[Error]:[Scene] SemanticScene.cpp(137)::loadSemanticSceneDescriptor : SSD Load Failure! File with SemanticAttributes-provided name `data/scene_datasets/habitat-test-scenes/skokloster-castle.scn` exists but failed to load.
2024-05-02 14:48:37,360 Initializing task Nav-v0
2024-05-02 14:48:46,902 Video created: /home/david/Desktop/EPFL/comm_proj/com304-go2/simulation/simulation/output/skokloster-castle.glb_3662.mp4
  0%|          | 0/78 [00:00<?, ?it/s]IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (855, 256) to (864, 256) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).
[swscaler @ 0x5555555dff40] Warning: data is not aligned! This can lead to a speed loss
100%|██████████